# Generating with PreTrained AMT Version

In this notebook, I will will be writing code to pull the AMT from Hugging Face then using it here

### Links : 
- https://huggingface.co/docs/transformers/en/quicktour

In [1]:
# Load model directly
from transformers import AutoModel
model = AutoModel.from_pretrained("stanford-crfm/music-small-ar-inter-100k")

/share/pkg.8/academic-ml/fall-2024/install/fall-2024-pyt/lib/python3.11/site-packages/huggingface_hub/file_download.py:1150: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
/usr4/cs640/rakin374/.local/lib/python3.11/site-packages/transformers/modeling_utils.py:446: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless 

## Code From Thickstun
- https://colab.research.google.com/drive/1HCQDtGFwROpHRqcmZbV0byqbxDb74YGu?usp=sharing#scrollTo=PlMSkS-1qJyj

In [10]:
# !git clone https://github.com/jthickstun/anticipation.git
# !pip install ./anticipation
# !pip install -r anticipation/requirements.txt

Cloning into 'anticipation'...
remote: Enumerating objects: 1343, done.
remote: Counting objects: 100% (757/757), done.
remote: Compressing objects: 100% (208/208), done.
remote: Total 1343 (delta 575), reused 714 (delta 548), pack-reused 586 (from 1)
Receiving objects: 100% (1343/1343), 56.04 MiB | 25.40 MiB/s, done.
Resolving deltas: 100% (898/898), done.
Defaulting to user installation because normal site-packages is not writeable
Processing ./anticipation
  Preparing metadata (setup.py) ... done
  Created wheel for anticipation: filename=anticipation-1.0-py3-none-any.whl size=18680 sha256=4544b5065f0169fbd90e045dfc29e8379999860cc0bdef17d6fbe13618d5f87a
  Stored in directory: /scratch/1139174.1.academic-gpu/pip-ephem-wheel-cache-ufdu3ok8/wheels/dd/41/11/84cee4b6b78c0052553fe37cf06402e29a87c692fb302c3cf3
Successfully built anticipation
Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 112.3/112.3 kB 9.0 MB/s eta

In [4]:
# ls
!ls

01_Variational_AutoEncoder.ipynb		   tmp.mid
02_Vector_Quantized_Variational_AutoEncoder.ipynb  tmp.wav
Data_Exploration_Aquila.ipynb			   tmp2.wav
Facebook_Dit_Exploration.ipynb			   tmp3.wav
Lakh_Statistics_2.ipynb				   tmp4.wav
Lakh_Vectorization.ipynb			   tmp5.wav
Using_AMT_Carina.ipynb				   tmp6.wav
anticipation					   tmpp.wav
fluidsynth.raw					   transfomers.ipynb
statistics.pkl


In [7]:
import sys,time
import os 
import midi2audio
import transformers
from transformers import AutoModelForCausalLM

from IPython.display import Audio

from anticipation import ops
from anticipation.sample import generate
from anticipation.tokenize import extract_instruments
from anticipation.convert import events_to_midi,midi_to_events
from anticipation.visuals import visualize
from anticipation.config import *
from anticipation.vocab import *

DATA_PATH = "../data/"
import torch
device = torch.device('cuda:0')

In [28]:
!pip3 install pyfluidsynth

Defaulting to user installation because normal site-packages is not writeable


In [16]:
fs = midi2audio.FluidSynth('../../FluidR3_GM.sf2')

In [30]:

ls

01_Variational_AutoEncoder.ipynb                   tmp.mid
02_Vector_Quantized_Variational_AutoEncoder.ipynb  tmp.wav
Data_Exploration_Aquila.ipynb                      tmp2.wav
Facebook_Dit_Exploration.ipynb                     tmp3.wav
Lakh_Statistics_2.ipynb                            tmp4.wav
Lakh_Vectorization.ipynb                           tmp5.wav
Using_AMT_3.ipynb                                  tmp6.wav
anticipation/                                      tmpp.wav
fluidsynth.raw                                     transfomers.ipynb
statistics.pkl


In [1]:
import fluidsynth

# Create a FluidSynth instance and load a SoundFont

fs = fluidsynth.Synth()
fs.start()
fs.sfload('../../FluidR3_GM.sf2')  # Provide the correct path to your SoundFont file

# Convert the MIDI file to audio (WAV)
fs.midi_to_audio('tmp.mid', 'tmp.wav')

AttributeError: module 'fluidsynth' has no attribute 'Synth'

In [13]:
SMALL_MODEL = 'stanford-crfm/music-small-800k'     # faster inference, worse sample quality
MEDIUM_MODEL = 'stanford-crfm/music-medium-800k'   # slower inference, better sample quality
LARGE_MODEL = 'stanford-crfm/music-large-800k'     # slowest inference, best sample quality

# load an anticipatory music transformer
model = AutoModelForCausalLM.from_pretrained(SMALL_MODEL).cuda()

os.environ['FLUIDSYNTH_PATH'] = '/projectnb/cs505aw/projects/bb/fluidsynth'
os.environ['LD_LIBRARY_PATH'] = '/projectnb/cs505aw/projects/bb/fluidsynth/lib64:' + os.environ.get('LD_LIBRARY_PATH', '')

# a MIDI synthesizer
fs = midi2audio.FluidSynth('../../FluidR3_GM.sf2')

# the MIDI synthesis script
def synthesize(fs, tokens):
    mid = events_to_midi(tokens)
    mid.save('tmp.mid')
    print(f"MIDI file saved with {len(tokens)} events.")
    fs.midi_to_audio('tmp.mid', 'tmp.wav')
    return 'tmp.wav'

Some weights of the model checkpoint at stanford-crfm/music-small-800k were not used when initializing GPT2LMHeadModel: ['token_out_embeddings']
- This IS expected if you are initializing GPT2LMHeadModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing GPT2LMHeadModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [14]:
import os
length = 10
os.environ['PATH'] = '../../fluidsynth/bin:' + os.environ['PATH']
unconditional_tokens = generate(model, start_time=0, end_time=length, top_p=.98)
Audio(synthesize(fs, unconditional_tokens))

 98%|█████████▊| 982/1000 [00:40<00:00, 24.27it/s]


MIDI file saved with 1035 events.
FluidSynth runtime version 2.4.0
Copyright (C) 2000-2024 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

Rendering audio to file 'tmp.wav'..


In [ ]:
## Scratch Space Below

In [10]:
Audio(DATA_PATH + "PinkPanther60.wav") # This works proving I'm just having trouble with the synthesis


In [8]:
ls ../data/

PinkPanther60.wav     cifar-10-python.tar.gz  clean_midi.tar.gz
cifar-10-batches-py/  clean_midi/
